In [6]:
from transformers import AutoTokenizer
from bertviz.transformers_neuron_view import BertModel
from bertviz.neuron_view import show

model_ckpt = "bert-base-uncased"
tokenizer = AutoTokenizer.from_pretrained(model_ckpt)
model=BertModel.from_pretrained(model_ckpt)
text="time files like an arrow"
show(model, "bert", tokenizer, text, display_mode="light", layer=0, head=8)

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [1]:
from transformers import AutoTokenizer
model_ckpt = "bert-base-uncased"
text="time fileds like an arrow"
tokenizer = AutoTokenizer.from_pretrained(model_ckpt)

In [2]:
inputs = tokenizer(text, return_tensors="pt", add_special_tokens=False)
inputs.input_ids

tensor([[2051, 6406, 2015, 2066, 2019, 8612]])

In [3]:
from torch import nn
from transformers import AutoConfig

config = AutoConfig.from_pretrained(model_ckpt)
token_emb = nn.Embedding(config.vocab_size, config.hidden_size)
token_emb

Embedding(30522, 768)

In [5]:
inputs_embeds = token_emb(inputs.input_ids)
inputs_embeds.size()

torch.Size([1, 6, 768])

In [6]:
import torch
from math import sqrt

query = key = value = inputs_embeds
dim_k = key.size(-1)
scores = torch.bmm(query, key.transpose(1, 2)) / sqrt(dim_k)
scores.size()

torch.Size([1, 6, 6])

In [7]:
import torch.nn.functional as F

weights = F.softmax(scores, dim=-1)
weights.sum(dim=-1)

tensor([[1., 1., 1., 1., 1., 1.]], grad_fn=<SumBackward1>)

In [8]:
attn_outputs = torch.bmm(weights, value)
attn_outputs.shape

torch.Size([1, 6, 768])

In [9]:
def scaled_dot_product_attention(query, key, value):
    dim_k = query.size(-1)
    scores = torch.bmm(query, key.transpose(1, 2)) / sqrt(dim_k)
    weights = F.softmax(scores, dim=-1)
    return torch.bmm(weights, value)

In [15]:
class AttentionHead(nn.Module):
    def __init__(self, embed_dim, head_dim):
        super().__init__()
        self.q = nn.Linear(embed_dim, head_dim)
        self.k = nn.Linear(embed_dim, head_dim)
        self.v = nn.Linear(embed_dim, head_dim)

    def forward(self, hidden_state):
        attn_outputs = scaled_dot_product_attention(
            self.q(hidden_state), self.k(hidden_state), self.v(hidden_state))
        return attn_outputs

In [16]:
class MultiHeadAttention(nn.Module):
    def __init__(self, config):
        super().__init__()
        embed_dim = config.hidden_size
        num_heads = config.num_attention_heads
        head_dim = embed_dim // num_heads
        self.heads = nn.ModuleList(
            [AttentionHead(embed_dim, head_dim) for _ in range(num_heads)]
        )
        self.output_linear = nn.Linear(embed_dim, embed_dim)

    def forward(self, hidden_state):
        x = torch.cat([h(hidden_state) for h in self.heads], dim=-1)
        x = self.output_linear(x)
        return x

In [17]:
multihead_attn = MultiHeadAttention(config)
attn_output = multihead_attn(inputs_embeds)
attn_output.size()

torch.Size([1, 6, 768])

In [18]:
from bertviz import head_view
from transformers import AutoModel

model = AutoModel.from_pretrained(model_ckpt, output_attentions=True)

sentence_a = "time files like an arrow"
sentence_b = "fruit files like a banana"

viz_inputs=tokenizer(sentence_a, sentence_b, return_tensors="pt")
attention=model(**viz_inputs).attentions
sentence_b_start=(viz_inputs.token_type_ids==0).sum(dim=1)
tokens=tokenizer.convert_ids_to_tokens(viz_inputs.input_ids[0])

head_view(attention, tokens, sentence_b_start, heads=[8])

model.safetensors:   0%|          | 0.00/440M [00:00<?, ?B/s]

c:\Users\BCML\anaconda3\envs\study\lib\site-packages\huggingface_hub\file_download.py:149: UserWarning: `huggingface_hub` cache-system uses symlinks by default to efficiently store duplicated files but your machine does not support them in C:\Users\BCML\.cache\huggingface\hub\models--bert-base-uncased. Caching files will still work but in a degraded version that might require more space on your disk. This warning can be disabled by setting the `HF_HUB_DISABLE_SYMLINKS_WARNING` environment variable. For more details, see https://huggingface.co/docs/huggingface_hub/how-to-cache#limitations.
To support symlinks on Windows, you either need to activate Developer Mode or to run Python as an administrator. In order to see activate developer mode, see this article: https://docs.microsoft.com/en-us/windows/apps/get-started/enable-your-device-for-development
  warnings.warn(message)


<IPython.core.display.Javascript object>

3.2.2 피드 포워드 층

In [23]:
class FeedForward(nn.Module):
    def __init__(self, config):
        super().__init__()
        self.linear_1 = nn.Linear(config.hidden_size, config.intermediate_size)
        self.linear_2 = nn.Linear(config.intermediate_size, config.hidden_size)
        self.gelu=nn.GELU()
        self.dropout=nn.Dropout(config.hidden_dropout_prob)

    def forward(self, x):
        x = self.linear_1(x)
        x = self.gelu(x)
        x = self.linear_2(x)
        x = self.dropout(x)
        return x

In [24]:
feed_forward = FeedForward(config)
ff_outputs = feed_forward(attn_outputs)
ff_outputs.size()

torch.Size([1, 6, 768])

3.2.3 층 정규화 추가하기
- 사전 층 정규화

In [25]:
class TransformerEncoderLayer(nn.Module):
    def __init__(self, config):
        super().__init__()
        self.layer_norm_1=nn.LayerNorm(config.hidden_size)
        self.layer_norm_2=nn.LayerNorm(config.hidden_size)
        self.attention=MultiHeadAttention(config)
        self.feed_forward=FeedForward(config)
    
    def forward(self, x):
        # 층 정규화를 적용하고 입력을 쿼리, 키, 값으로 복사한다.
        hidden_state = self.layer_norm_1(x)
        # 어텐션에 스킵 연결을 적용한다.
        x = x+self.attention(hidden_state)
        # 스킵 연결과 피드 포워드 층을 적용한다.
        x=x+self.feed_forward(self.layer_norm_2(x))
        return x

In [26]:
encoder_layer = TransformerEncoderLayer(config)
inputs_embeds.shape, encoder_layer(inputs_embeds).size()

(torch.Size([1, 6, 768]), torch.Size([1, 6, 768]))

3.2.4 위치 임베딩

In [31]:

class Embeddings(nn.Module):
    def __init__(self, config):
        super().__init__()
        self.token_embeddings = nn.Embedding(config.vocab_size,
                                             config.hidden_size)
        self.position_embeddings = nn.Embedding(config.max_position_embeddings,
                                                config.hidden_size)
        self.layer_norm = nn.LayerNorm(config.hidden_size, eps=1e-12)
        self.dropout = nn.Dropout()

    def forward(self, input_ids):
        # 입력 시퀀스에 대해 위치 ID를 만듭니다.
        seq_length = input_ids.size(1)
        position_ids = torch.arange(seq_length, dtype=torch.long).unsqueeze(0)
        # 토큰 임베딩과 위치 임베딩을 만듭니다.
        token_embeddings = self.token_embeddings(input_ids)
        position_embeddings = self.position_embeddings(position_ids)
        # 토큰 임베딩과 위치 임베딩을 합칩니다.
        embeddings = token_embeddings + position_embeddings
        embeddings = self.layer_norm(embeddings)
        embeddings = self.dropout(embeddings)
        return embeddings

embedding_layer = Embeddings(config)
embedding_layer(inputs.input_ids).size()

torch.Size([1, 6, 768])

In [32]:
class TransformerEncoder(nn.Module):
    def __init__(self, config):
        super().__init__()
        self.embeddings = Embeddings(config)
        self.layers=nn.ModuleList([
            TransformerEncoderLayer(config) for _ in range(config.num_hidden_layers)
        ])
    def forward(self, x):
        x=self.embeddings(x)
        for layer in self.layers:
            x=layer(x)
        return x
    
encoder=TransformerEncoder(config)
encoder(inputs.input_ids).size()

torch.Size([1, 6, 768])

3.2.5 분류 헤드 추가하기

In [33]:
class TransformerForSequenceClassification(nn.Module):
    def __init__(self, config):
        super().__init__()
        self.encoder = TransformerEncoder(config)
        self.dropout = nn.Dropout(config.hidden_dropout_prob)
        self.classifier = nn.Linear(config.hidden_size, config.num_labels)
    
    def forward(self, x):
        x=self.encoder(x)[:, 0, :]# [CLS] 토큰의 은닉 상태를 선택한다.
        x=self.dropout(x)
        x=self.classifier(x)
        return x
    
# 모델을 초기화하기 전 예측하려는 클래스 개수를 정의한다.
config.num_labels=3
encoder_classifier=TransformerForSequenceClassification(config)
encoder_classifier(inputs.input_ids).size()

torch.Size([1, 3])

3.3 디코더

In [34]:
seq_len = inputs.input_ids.size(-1)
mask = torch.tril(torch.ones(seq_len, seq_len)).unsqueeze(0)
mask[0]

tensor([[1., 0., 0., 0., 0., 0.],
        [1., 1., 0., 0., 0., 0.],
        [1., 1., 1., 0., 0., 0.],
        [1., 1., 1., 1., 0., 0.],
        [1., 1., 1., 1., 1., 0.],
        [1., 1., 1., 1., 1., 1.]])

In [35]:
scores.masked_fill(mask==0, -float("inf"))

tensor([[[ 3.1567e+01,        -inf,        -inf,        -inf,        -inf,
                 -inf],
         [ 1.0483e-01,  2.5579e+01,        -inf,        -inf,        -inf,
                 -inf],
         [ 7.3063e-02, -3.7904e-02,  3.0359e+01,        -inf,        -inf,
                 -inf],
         [-9.2477e-03, -1.8487e+00,  1.1952e+00,  2.6763e+01,        -inf,
                 -inf],
         [ 5.3493e-01, -3.2608e-01, -4.6389e-01, -9.8105e-01,  2.8892e+01,
                 -inf],
         [-1.2527e+00, -6.0501e-01,  7.1155e-01,  9.2441e-01, -3.4281e-01,
           2.7984e+01]]], grad_fn=<MaskedFillBackward0>)

In [36]:
def scaled_dot_product_attention(query, key, value, mask=None):
    dim_k = query.size(-1)
    scores = torch.bmm(query, key.transpose(1, 2)) / sqrt(dim_k)
    if mask is not None:
        scores = scores.masked_fill(mask==0, float("-inf"))
        weights = F.softmax(scores, dim=-1)
        return weights.bmm(value)